In [8]:
%%time

import os
import pandas as pd
import numpy as np
import scipy.optimize as optimize
#data reading and cleaning
import gc
from tqdm import tqdm
items = pd.read_csv('Data/items.csv')
samples = pd.read_csv('Data/samples.csv')
test = pd.read_csv('Data/test.csv')
train = pd.read_csv('Data/train.csv')
users = pd.read_csv('Data/users.csv')


train_cols ={
    'User ID':'usr_id',
    'Item1 ID':'item1_id',
    'Item2 ID':'item2_id',
    'Preference':'preference'
}
train = train.rename(columns=train_cols)

test_cols ={
    'User ID':'usr_id',
    'Item1 ID':'item1_id',
    'Item2 ID':'item2_id',
}
test = test.rename(columns=test_cols)

users_cols ={
    'User ID':'usr_id',
    ' Education':'education',
    ' Age':'age',
    ' Gender':'gender',
    ' Region':'region'
}
users = users.rename(columns=users_cols)

# data merging

item1_cols ={
    'Item ID':'item1_id',
    ' BodyType':'body_type_1',
    ' Transmission':'transmission_1',
    ' Engin Capacity':'engin_capacity_1',
    ' Fuel Consumed':'fuel_consumed_1'
}

item2_cols ={
    'Item ID':'item2_id',
    ' BodyType':'body_type_2',
    ' Transmission':'transmission_2',
    ' Engin Capacity':'engin_capacity_2',
    ' Fuel Consumed':'fuel_consumed_2'
}

def find_winner():
    k = pd.read_csv('Data/train.csv')
    train_cols ={
        'User ID':'usr_id',
        'Item1 ID':'item1_id',
        'Item2 ID':'item2_id',
        'Preference':'preference'
    }
    k = k.rename(columns=train_cols)

    win=list()
    for index in k.index:
        if k.preference[index] ==0:
            win.append(k.item1_id[index])
        else:
            win.append(k.item2_id[index])
    k['win'] = win
    
    return k

def number_count(k):
    k = k.drop(columns=['preference','win'])

    p1 = k.pivot_table(index = ['usr_id'],columns=['item1_id'], aggfunc='count').fillna(0)
    p2= k.pivot_table(index = ['usr_id'],columns=['item2_id'], aggfunc='count').fillna(0)

    p1.columns = p1.columns.to_series().str.join('_')
    p2.columns = p2.columns.to_series().str.join('_')

    p1.columns = ['1_count','2_count','3_count','4_count','5_count',
                 '6_count','7_count','8_count','9_count','10_count']

    p2.columns = ['1_count','2_count','3_count','4_count','5_count',
                 '6_count','7_count','8_count','9_count','10_count']
    del p1.index.name, p2.index.name
    return p1+p2

def winner_count(k):
    k = k.drop(columns=['item1_id','item2_id'])

    result = k.pivot_table(index = ['usr_id'],columns=['win'], aggfunc='count')

    result.columns.to_series().str.join('_')
    del result.index.name

    #result.columns = result.columns.get_level_values(0)
    result.columns = ['1_count','2_count','3_count','4_count','5_count',
                 '6_count','7_count','8_count','9_count','10_count']
    return result

def occur_rate(k):
    k = (k/9).fillna(0)
    k['usr_id'] = k.index
    
    return k

def win_rate(w_count,n_count):
    k = (w_count/n_count).fillna(0)
    k.columns = ['1_win','2_win','3_win','4_win','5_win',
                '6_win','7_win','8_win','9_win','10_win']
    k['usr_id'] = k.index
    
    return k
    
def max_f(params):
    r1,r2,r3,r4,r5,r6,r7,r8,r9,r10 = params
    R = [r1,r2,r3,r4,r5,r6,r7,r8,r9,r10]
    index:int
    result = 1
    for index in data.index:
        result *= R[data.win[index]-1] / (R[data.item1_id[index]-1] + R[data.item2_id[index]-1])
        
    return -result


#calculate occur times and win rate

winner_list = find_winner()
n_count = number_count(winner_list)
w_count = winner_count(winner_list)
occur = occur_rate(n_count)
win = win_rate(w_count,n_count)

#concat train and test
df = pd.concat([train,test])
item_1 = items.copy().rename(columns = item1_cols)
item_2 = items.copy().rename(columns = item2_cols)
df = pd.merge(df,users, on =['usr_id'])
df = pd.merge(df,item_1, on =['item1_id'])
df = pd.merge(df,item_2, on =['item2_id'])
df.shape

del item_1,item_2
gc.collect()
#feature generation
#df = pd.merge(df,occur,on = ['usr_id'])
df = pd.merge(df,win,on = ['usr_id'])
df['engin2_bigger'] = 0
df.engin2_bigger[df.engin_capacity_1==df.engin_capacity_2] = 2
df.engin2_bigger[df.engin_capacity_1>df.engin_capacity_2] = 0
df.engin2_bigger[df.engin_capacity_1<df.engin_capacity_2] = 1

del n_count,w_count,occur,win
gc.collect()

#calculate likelyhood

r_cobyla_list = list()
r_powell_list = list()
initial_guess = [1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
for i in tqdm(range(60)):
    data = winner_list[winner_list['usr_id']==i]
    result_cobyla = optimize.minimize(max_f, initial_guess, method='COBYLA')
    result_powell = optimize.minimize(max_f, initial_guess, method='Powell')
    r_cobyla_list.append(result_cobyla.x - result_cobyla.x.min() + 1)
    r_powell_list.append(result_powell.x - result_powell.x.min()+1)
    

powell = list()
cobylab = list()
for index in tqdm(df.index):
    R_powell = r_powell_list[df.usr_id[index]-1]
    R_cobylab = r_cobyla_list[df.usr_id[index]-1]
    prob_p = R_powell[df.item2_id[index]-1] / (R_powell[df.item1_id[index]-1] + R_powell[df.item2_id[index]-1])
    prob_c = R_powell[df.item2_id[index]-1] / (R_powell[df.item1_id[index]-1] + R_powell[df.item2_id[index]-1])
    
    powell.append(prob_p)
    cobylab.append(prob_c)
    

df['powell'] = powell
#df['cobylab'] = cobylab

del powell#, cobylab
gc.collect()
#split train test
test = df[df.preference.isna()]
train = df[df.preference.isna()==0]

label = train.preference

train = train.drop(columns=['preference'])
test = test.drop(columns=['preference'])

#train = train.drop(columns=['preference','usr_id','item1_id','item2_id'])
#test = test.drop(columns=['preference','usr_id','item1_id','item2_id'])
#train_test split

from sklearn.model_selection import train_test_split
train_data, valid_data, train_target, valid_target = train_test_split(train, label, test_size=0.33, random_state=9)



/usr/local/lib/python3.6/site-packages/ipykernel_launcher.py:156: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/usr/local/lib/python3.6/site-packages/ipykernel_launcher.py:157: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/usr/local/lib/python3.6/site-packages/ipykernel_launcher.py:158: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
 13%|█▎        | 8/60 [00:23<02:32,  2.93s/it]/usr/local/lib/python3.6/site-packages/ipykernel_launcher.py:128: RuntimeWarning: divide by zero encountered in do

CPU times: user 3min 37s, sys: 1.22 s, total: 3min 38s
Wall time: 3min 44s


In [6]:
from sklearn.metrics import accuracy_score
from hyperopt import fmin, tpe, hp, rand
from sklearn.linear_model import LogisticRegression   

parameter_space_logit ={
    # loguniform表示该参数取对数后符合均匀分布
    'C':hp.loguniform("C", np.log(1), np.log(100)),
    #'dual':hp.choice('dual',[1,0]),
    'penalty':hp.choice('penalty',['l1','l2']),
}

count = 0

def function(args):
    print(args)

    # **可以把dict转换为关键字参数，可以大大简化复杂的函数调用
    clf = LogisticRegression(**args)

    # 训练模型
    clf.fit(train_data,train_target)

    # 预测测试集
    prediction = clf.predict(valid_data)

    global count
    count = count + 1
    score = accuracy_score(valid_target, prediction)
    print("第%s次，测试集正确率为：" % str(count),score)

    # 由于hyperopt仅提供fmin接口，因此如果要求最大值，则需要取相反数
    return -score

# algo指定搜索算法，目前支持以下算法：
# ①随机搜索(hyperopt.rand.suggest)
# ②模拟退火(hyperopt.anneal.suggest)
# ③TPE算法（hyperopt.tpe.suggest，算法全称为Tree-structured Parzen Estimator Approach）
# max_evals指定枚举次数上限，即使第max_evals次枚举仍未能确定全局最优解，也要结束搜索，返回目前搜索到的最优解
best = fmin(function, parameter_space_logit, algo=tpe.suggest, max_evals=10000)

# best["kernel"]返回的是数组下标，因此需要把它还原回来
penalty_list = ['l1','l2']
best["penalty"] = penalty_list[best["penalty"]]

print("最佳参数为：",best)


{'C': 3.907782986845508, 'penalty': 'l1'}
第1次，测试集正确率为： 0.623059866962306
{'C': 2.093037090789181, 'penalty': 'l1'}
第2次，测试集正确率为： 0.6252771618625277
{'C': 1.9790397193693614, 'penalty': 'l1'}
第3次，测试集正确率为： 0.6274944567627494
{'C': 3.696170130053251, 'penalty': 'l1'}
第4次，测试集正确率为： 0.623059866962306
{'C': 3.957559449604628, 'penalty': 'l1'}
第5次，测试集正确率为： 0.6252771618625277
{'C': 58.78778169952171, 'penalty': 'l2'}
第6次，测试集正确率为： 0.6075388026607539
{'C': 1.2887541990974196, 'penalty': 'l2'}
第7次，测试集正确率为： 0.623059866962306
{'C': 40.3523079900207, 'penalty': 'l2'}
第8次，测试集正确率为： 0.6119733924611973
{'C': 54.177299192514305, 'penalty': 'l1'}
第9次，测试集正确率为： 0.6097560975609756
{'C': 27.191226421088622, 'penalty': 'l2'}
第10次，测试集正确率为： 0.6119733924611973
{'C': 19.403355172710846, 'penalty': 'l2'}
第11次，测试集正确率为： 0.6164079822616408
{'C': 11.962182902614424, 'penalty': 'l1'}
第12次，测试集正确率为： 0.6164079822616408
{'C': 5.446359184966132, 'penalty': 'l2'}
第13次，测试集正确率为： 0.6252771618625277
{'C': 4.855217386446892, 'penalt

第112次，测试集正确率为： 0.6274944567627494
{'C': 5.5054718165146435, 'penalty': 'l1'}
第113次，测试集正确率为： 0.6252771618625277
{'C': 7.8337904688978615, 'penalty': 'l1'}
第114次，测试集正确率为： 0.6164079822616408
{'C': 2.552647336064416, 'penalty': 'l2'}
第115次，测试集正确率为： 0.6252771618625277
{'C': 1.014819265241546, 'penalty': 'l1'}
第116次，测试集正确率为： 0.6252771618625277
{'C': 6.581711714914493, 'penalty': 'l1'}
第117次，测试集正确率为： 0.6274944567627494
{'C': 16.33252872662355, 'penalty': 'l1'}
第118次，测试集正确率为： 0.6119733924611973
{'C': 2.038895660724763, 'penalty': 'l1'}
第119次，测试集正确率为： 0.6252771618625277
{'C': 13.052832729368024, 'penalty': 'l2'}
第120次，测试集正确率为： 0.6186252771618626
{'C': 36.07151550696951, 'penalty': 'l1'}
第121次，测试集正确率为： 0.6075388026607539
{'C': 1.7885603703483846, 'penalty': 'l1'}
第122次，测试集正确率为： 0.6252771618625277
{'C': 1.4463591778158826, 'penalty': 'l1'}
第123次，测试集正确率为： 0.623059866962306
{'C': 14.733532737992272, 'penalty': 'l1'}
第124次，测试集正确率为： 0.614190687361419
{'C': 68.5634747506807, 'penalty': 'l2'}
第125次，测试集

第220次，测试集正确率为： 0.6252771618625277
{'C': 12.669795681899632, 'penalty': 'l2'}
第221次，测试集正确率为： 0.6186252771618626
{'C': 1.9002520376546037, 'penalty': 'l1'}
第222次，测试集正确率为： 0.6274944567627494
{'C': 7.169304127062821, 'penalty': 'l1'}
第223次，测试集正确率为： 0.623059866962306
{'C': 2.861279057121653, 'penalty': 'l1'}
第224次，测试集正确率为： 0.6252771618625277
{'C': 2.1333353650971643, 'penalty': 'l1'}
第225次，测试集正确率为： 0.6252771618625277
{'C': 1.1129011067850283, 'penalty': 'l1'}
第226次，测试集正确率为： 0.6252771618625277
{'C': 3.472635660575004, 'penalty': 'l1'}
第227次，测试集正确率为： 0.6252771618625277
{'C': 3.194860616149557, 'penalty': 'l2'}
第228次，测试集正确率为： 0.623059866962306
{'C': 58.70937663899254, 'penalty': 'l1'}
第229次，测试集正确率为： 0.6097560975609756
{'C': 4.478190163548487, 'penalty': 'l1'}
第230次，测试集正确率为： 0.623059866962306
{'C': 9.578866739678155, 'penalty': 'l1'}
第231次，测试集正确率为： 0.6186252771618626
{'C': 6.921058853502153, 'penalty': 'l1'}
第232次，测试集正确率为： 0.6274944567627494
{'C': 4.127185101096137, 'penalty': 'l2'}
第233次，测试集正确

第330次，测试集正确率为： 0.623059866962306
{'C': 6.419431634844573, 'penalty': 'l1'}
第331次，测试集正确率为： 0.6274944567627494
{'C': 11.871019181405833, 'penalty': 'l1'}
第332次，测试集正确率为： 0.6164079822616408
{'C': 2.9857205688901165, 'penalty': 'l1'}
第333次，测试集正确率为： 0.6274944567627494
{'C': 2.796009954673041, 'penalty': 'l1'}
第334次，测试集正确率为： 0.623059866962306
{'C': 1.9398464634632595, 'penalty': 'l2'}
第335次，测试集正确率为： 0.623059866962306
{'C': 1.1919521362740737, 'penalty': 'l1'}
第336次，测试集正确率为： 0.6252771618625277
{'C': 3.479256152579274, 'penalty': 'l1'}
第337次，测试集正确率为： 0.6252771618625277
{'C': 99.44141093192796, 'penalty': 'l1'}
第338次，测试集正确率为： 0.6075388026607539
{'C': 2.532207266098144, 'penalty': 'l1'}
第339次，测试集正确率为： 0.623059866962306
{'C': 5.138077245109092, 'penalty': 'l1'}
第340次，测试集正确率为： 0.6252771618625277
{'C': 3.906365092070409, 'penalty': 'l1'}
第341次，测试集正确率为： 0.623059866962306
{'C': 7.612815219495904, 'penalty': 'l1'}
第342次，测试集正确率为： 0.623059866962306
{'C': 2.433471720311212, 'penalty': 'l2'}
第343次，测试集正确率为：

第439次，测试集正确率为： 0.6274944567627494
{'C': 5.758484653913202, 'penalty': 'l1'}
第440次，测试集正确率为： 0.6274944567627494
{'C': 5.609419633451096, 'penalty': 'l1'}
第441次，测试集正确率为： 0.6274944567627494
{'C': 9.840436224744932, 'penalty': 'l1'}
第442次，测试集正确率为： 0.6164079822616408
{'C': 1.8504278414115076, 'penalty': 'l1'}
第443次，测试集正确率为： 0.6252771618625277
{'C': 3.8338961176470536, 'penalty': 'l2'}
第444次，测试集正确率为： 0.623059866962306
{'C': 4.889651015958163, 'penalty': 'l1'}
第445次，测试集正确率为： 0.623059866962306
{'C': 1.9328909112152288, 'penalty': 'l1'}
第446次，测试集正确率为： 0.6274944567627494
{'C': 3.9750024097271512, 'penalty': 'l1'}
第447次，测试集正确率为： 0.623059866962306
{'C': 10.835118442273433, 'penalty': 'l1'}
第448次，测试集正确率为： 0.6164079822616408
{'C': 1.2151754462418523, 'penalty': 'l1'}
第449次，测试集正确率为： 0.6252771618625277
{'C': 8.133800294865479, 'penalty': 'l1'}
第450次，测试集正确率为： 0.6164079822616408
{'C': 4.21758515591954, 'penalty': 'l1'}
第451次，测试集正确率为： 0.623059866962306
{'C': 8.933398266115637, 'penalty': 'l1'}
第452次，测试集正确

...

第8384次，测试集正确率为： 0.623059866962306
{'C': 6.40687673184288, 'penalty': 'l1'}
第8385次，测试集正确率为： 0.6274944567627494
{'C': 5.825716044111092, 'penalty': 'l1'}
第8386次，测试集正确率为： 0.6274944567627494
{'C': 6.256460152277339, 'penalty': 'l1'}
第8387次，测试集正确率为： 0.6274944567627494
{'C': 1.755950794359343, 'penalty': 'l1'}
第8388次，测试集正确率为： 0.6274944567627494
{'C': 4.361461016598668, 'penalty': 'l1'}
第8389次，测试集正确率为： 0.623059866962306
{'C': 5.5777964554848305, 'penalty': 'l1'}
第8390次，测试集正确率为： 0.6274944567627494
{'C': 5.774278263598281, 'penalty': 'l1'}
第8391次，测试集正确率为： 0.6274944567627494
{'C': 3.7408039379781295, 'penalty': 'l1'}
第8392次，测试集正确率为： 0.623059866962306
{'C': 4.298480932307077, 'penalty': 'l1'}
第8393次，测试集正确率为： 0.623059866962306
{'C': 4.353474571871332, 'penalty': 'l1'}
第8394次，测试集正确率为： 0.623059866962306
{'C': 5.162924416981749, 'penalty': 'l1'}
第8395次，测试集正确率为： 0.6252771618625277
{'C': 6.3415133944679845, 'penalty': 'l1'}
第8396次，测试集正确率为： 0.6274944567627494
{'C': 7.087169237221429, 'penalty': 'l1'}
第8

第8491次，测试集正确率为： 0.6252771618625277
{'C': 5.678567054055838, 'penalty': 'l1'}
第8492次，测试集正确率为： 0.6274944567627494
{'C': 5.993050302064475, 'penalty': 'l1'}
第8493次，测试集正确率为： 0.6274944567627494
{'C': 6.035160783890481, 'penalty': 'l1'}
第8494次，测试集正确率为： 0.6252771618625277
{'C': 6.200968758175778, 'penalty': 'l1'}
第8495次，测试集正确率为： 0.6274944567627494
{'C': 2.72842821109165, 'penalty': 'l1'}
第8496次，测试集正确率为： 0.623059866962306
{'C': 5.130311667014255, 'penalty': 'l1'}
第8497次，测试集正确率为： 0.623059866962306
{'C': 5.716823389789658, 'penalty': 'l1'}
第8498次，测试集正确率为： 0.6274944567627494
{'C': 4.819346462345274, 'penalty': 'l1'}
第8499次，测试集正确率为： 0.623059866962306
{'C': 4.885761881680657, 'penalty': 'l1'}
第8500次，测试集正确率为： 0.623059866962306
{'C': 5.600510268927418, 'penalty': 'l1'}
第8501次，测试集正确率为： 0.6274944567627494
{'C': 4.997384716058146, 'penalty': 'l1'}
第8502次，测试集正确率为： 0.623059866962306
{'C': 3.795776442989238, 'penalty': 'l1'}
第8503次，测试集正确率为： 0.623059866962306
{'C': 5.83301210841422, 'penalty': 'l1'}
第8504次，

第8598次，测试集正确率为： 0.6274944567627494
{'C': 6.0122282633150785, 'penalty': 'l1'}
第8599次，测试集正确率为： 0.6252771618625277
{'C': 3.999218739702564, 'penalty': 'l1'}
第8600次，测试集正确率为： 0.623059866962306
{'C': 5.276321987914897, 'penalty': 'l1'}
第8601次，测试集正确率为： 0.6252771618625277
{'C': 4.890564408273161, 'penalty': 'l1'}
第8602次，测试集正确率为： 0.623059866962306
{'C': 5.35099645320022, 'penalty': 'l1'}
第8603次，测试集正确率为： 0.6252771618625277
{'C': 4.474736814849502, 'penalty': 'l1'}
第8604次，测试集正确率为： 0.623059866962306
{'C': 5.867968784840151, 'penalty': 'l1'}
第8605次，测试集正确率为： 0.6274944567627494
{'C': 6.055306674636715, 'penalty': 'l1'}
第8606次，测试集正确率为： 0.6274944567627494
{'C': 6.31753533579609, 'penalty': 'l1'}
第8607次，测试集正确率为： 0.6274944567627494
{'C': 4.585241289809241, 'penalty': 'l1'}
第8608次，测试集正确率为： 0.623059866962306
{'C': 6.042130116320011, 'penalty': 'l1'}
第8609次，测试集正确率为： 0.6252771618625277
{'C': 6.039008067807976, 'penalty': 'l1'}
第8610次，测试集正确率为： 0.6274944567627494
{'C': 4.535534218627934, 'penalty': 'l1'}
第861

{'C': 5.4496160159310865, 'penalty': 'l1'}
第8706次，测试集正确率为： 0.6252771618625277
{'C': 36.297169663733385, 'penalty': 'l1'}
第8707次，测试集正确率为： 0.6075388026607539
{'C': 5.239082127935043, 'penalty': 'l1'}
第8708次，测试集正确率为： 0.6252771618625277
{'C': 4.573600679296575, 'penalty': 'l1'}
第8709次，测试集正确率为： 0.623059866962306
{'C': 5.73308459395187, 'penalty': 'l1'}
第8710次，测试集正确率为： 0.6274944567627494
{'C': 5.5633137011409515, 'penalty': 'l1'}
第8711次，测试集正确率为： 0.6274944567627494
{'C': 6.171648284538644, 'penalty': 'l1'}
第8712次，测试集正确率为： 0.6274944567627494
{'C': 5.893233801447071, 'penalty': 'l1'}
第8713次，测试集正确率为： 0.6252771618625277
{'C': 4.353848205942649, 'penalty': 'l1'}
第8714次，测试集正确率为： 0.623059866962306
{'C': 6.253669394158958, 'penalty': 'l1'}
第8715次，测试集正确率为： 0.6274944567627494
{'C': 5.572110778364322, 'penalty': 'l1'}
第8716次，测试集正确率为： 0.6274944567627494
{'C': 5.441181551887467, 'penalty': 'l1'}
第8717次，测试集正确率为： 0.6252771618625277
{'C': 5.02206703902215, 'penalty': 'l1'}
第8718次，测试集正确率为： 0.623059866962306
{

KeyboardInterrupt: 

In [ ]:
test = test.drop(columns='preference')

In [27]:
%%time
  
classifier = LogisticRegression(C= 20.402633905230882, penalty= 'l1')  # 使用类，参数全是默认的  
classifier.fit(train_data, train_target)  # 训练数据来学习，不需要返回值  
#print(accuracy_score(valid_target, classifier.predict(valid_data)))

prediction = classifier.predict(test)

test["User-Item1-Item2"] = test['usr_id'].map(str)+'-'+test['item1_id'].map(str)+'-'+test['item2_id'].map(str)
test['Preference'] = prediction.astype(np.int8)

submission = test[['User-Item1-Item2','Preference']]

submission.to_csv('submission1_Logit.csv',index = False)

CPU times: user 72.1 ms, sys: 2.04 ms, total: 74.2 ms
Wall time: 73.2 ms


In [10]:
from sklearn.metrics import accuracy_score
from hyperopt import fmin, tpe, hp, rand
from sklearn.ensemble import RandomForestClassifier

parameter_space_forest ={
    # loguniform表示该参数取对数后符合均匀分布
    'max_depth':hp.randint("max_depth", 39)+1,
    'criterion':hp.choice('criterion',['gini','entropy']),
    'bootstrap':hp.choice('bootstrap',[1,0]),
    'n_estimators':hp.randint('n_estimators', 60)+1,
    'max_features':hp.uniform('max_features', 0.2, 0.8),
    'min_samples_leaf':hp.randint('min_samples_leaf',80)+1,
    'random_state':40
}

count = 0

def function(args):
    print(args)

    # **可以把dict转换为关键字参数，可以大大简化复杂的函数调用
    clf = RandomForestClassifier(**args)

    # 训练模型
    clf.fit(train_data,train_target)

    # 预测测试集
    prediction = clf.predict(valid_data)

    global count
    count = count + 1
    score = accuracy_score(valid_target, prediction)
    print("第%s次，测试集正确率为：" % str(count),score)

    # 由于hyperopt仅提供fmin接口，因此如果要求最大值，则需要取相反数
    return -score

# algo指定搜索算法，目前支持以下算法：
# ①随机搜索(hyperopt.rand.suggest)
# ②模拟退火(hyperopt.anneal.suggest)
# ③TPE算法（hyperopt.tpe.suggest，算法全称为Tree-structured Parzen Estimator Approach）
# max_evals指定枚举次数上限，即使第max_evals次枚举仍未能确定全局最优解，也要结束搜索，返回目前搜索到的最优解
best = fmin(function, parameter_space_forest, algo=tpe.suggest, max_evals=10000)

# best["kernel"]返回的是数组下标，因此需要把它还原回来
bootstrap_list = [1,0]
best["bootstrap"] = bootstrap_list[best["bootstrap"]]

criterion_list = ['gini','entropy']
best["criterion"] = criterion_list[best["criterion"]]

print("最佳参数为：",best)



{'bootstrap': 1, 'criterion': 'entropy', 'max_depth': 28, 'max_features': 0.6229509438945695, 'min_samples_leaf': 29, 'n_estimators': 42, 'random_state': 40}
第1次，测试集正确率为： 0.7028824833702882
{'bootstrap': 1, 'criterion': 'gini', 'max_depth': 28, 'max_features': 0.6286699230285098, 'min_samples_leaf': 34, 'n_estimators': 1, 'random_state': 40}
第2次，测试集正确率为： 0.6674057649667405
{'bootstrap': 1, 'criterion': 'gini', 'max_depth': 21, 'max_features': 0.6694894750869413, 'min_samples_leaf': 56, 'n_estimators': 27, 'random_state': 40}
第3次，测试集正确率为： 0.6762749445676275
{'bootstrap': 1, 'criterion': 'gini', 'max_depth': 34, 'max_features': 0.4194118099606775, 'min_samples_leaf': 26, 'n_estimators': 19, 'random_state': 40}
第4次，测试集正确率为： 0.7649667405764967
{'bootstrap': 1, 'criterion': 'gini', 'max_depth': 27, 'max_features': 0.3228064496449967, 'min_samples_leaf': 13, 'n_estimators': 36, 'random_state': 40}
第5次，测试集正确率为： 0.7694013303769401
{'bootstrap': 1, 'criterion': 'entropy', 'max_depth': 32, 'max_

{'bootstrap': 0, 'criterion': 'gini', 'max_depth': 39, 'max_features': 0.46413696358679063, 'min_samples_leaf': 78, 'n_estimators': 54, 'random_state': 40}
第45次，测试集正确率为： 0.6807095343680709
{'bootstrap': 1, 'criterion': 'entropy', 'max_depth': 18, 'max_features': 0.40117808268436617, 'min_samples_leaf': 40, 'n_estimators': 2, 'random_state': 40}
第46次，测试集正确率为： 0.6696230598669624
{'bootstrap': 0, 'criterion': 'gini', 'max_depth': 20, 'max_features': 0.5659834648049009, 'min_samples_leaf': 21, 'n_estimators': 37, 'random_state': 40}
第47次，测试集正确率为： 0.753880266075388
{'bootstrap': 1, 'criterion': 'gini', 'max_depth': 11, 'max_features': 0.3622329812563659, 'min_samples_leaf': 6, 'n_estimators': 6, 'random_state': 40}
第48次，测试集正确率为： 0.7804878048780488
{'bootstrap': 0, 'criterion': 'gini', 'max_depth': 38, 'max_features': 0.22953637974743185, 'min_samples_leaf': 3, 'n_estimators': 53, 'random_state': 40}
第49次，测试集正确率为： 0.8470066518847007
{'bootstrap': 1, 'criterion': 'entropy', 'max_depth': 38, '

第89次，测试集正确率为： 0.6651884700665188
{'bootstrap': 0, 'criterion': 'gini', 'max_depth': 20, 'max_features': 0.49950386584722073, 'min_samples_leaf': 33, 'n_estimators': 25, 'random_state': 40}
第90次，测试集正确率为： 0.7117516629711752
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 22, 'max_features': 0.22132374813829442, 'min_samples_leaf': 18, 'n_estimators': 22, 'random_state': 40}
第91次，测试集正确率为： 0.802660753880266
{'bootstrap': 0, 'criterion': 'gini', 'max_depth': 18, 'max_features': 0.3345552232165456, 'min_samples_leaf': 7, 'n_estimators': 59, 'random_state': 40}
第92次，测试集正确率为： 0.8248337028824834
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 36, 'max_features': 0.27410843506783295, 'min_samples_leaf': 44, 'n_estimators': 40, 'random_state': 40}
第93次，测试集正确率为： 0.7095343680709535
{'bootstrap': 0, 'criterion': 'gini', 'max_depth': 6, 'max_features': 0.35699140626296755, 'min_samples_leaf': 3, 'n_estimators': 29, 'random_state': 40}
第94次，测试集正确率为： 0.8137472283813747
{'bootstrap': 1, 'cri

第133次，测试集正确率为： 0.7184035476718403
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 22, 'max_features': 0.3035682852505776, 'min_samples_leaf': 10, 'n_estimators': 53, 'random_state': 40}
第134次，测试集正确率为： 0.8203991130820399
{'bootstrap': 0, 'criterion': 'gini', 'max_depth': 20, 'max_features': 0.2724574834613355, 'min_samples_leaf': 40, 'n_estimators': 55, 'random_state': 40}
第135次，测试集正确率为： 0.7028824833702882
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 16, 'max_features': 0.37808483198122766, 'min_samples_leaf': 3, 'n_estimators': 44, 'random_state': 40}
第136次，测试集正确率为： 0.8248337028824834
{'bootstrap': 0, 'criterion': 'gini', 'max_depth': 4, 'max_features': 0.39133943057290926, 'min_samples_leaf': 78, 'n_estimators': 27, 'random_state': 40}
第137次，测试集正确率为： 0.6762749445676275
{'bootstrap': 1, 'criterion': 'entropy', 'max_depth': 18, 'max_features': 0.26098080514130023, 'min_samples_leaf': 15, 'n_estimators': 21, 'random_state': 40}
第138次，测试集正确率为： 0.7827050997782705
{'bootstrap

第176次，测试集正确率为： 0.7871396895787139
{'bootstrap': 1, 'criterion': 'entropy', 'max_depth': 21, 'max_features': 0.23835111535392403, 'min_samples_leaf': 7, 'n_estimators': 15, 'random_state': 40}
第177次，测试集正确率为： 0.8159645232815964
{'bootstrap': 0, 'criterion': 'gini', 'max_depth': 21, 'max_features': 0.2009974425079454, 'min_samples_leaf': 9, 'n_estimators': 56, 'random_state': 40}
第178次，测试集正确率为： 0.835920177383592
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 21, 'max_features': 0.2715502766918283, 'min_samples_leaf': 52, 'n_estimators': 31, 'random_state': 40}
第179次，测试集正确率为： 0.7161862527716186
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 31, 'max_features': 0.7173011433218242, 'min_samples_leaf': 44, 'n_estimators': 32, 'random_state': 40}
第180次，测试集正确率为： 0.6962305986696231
{'bootstrap': 0, 'criterion': 'gini', 'max_depth': 30, 'max_features': 0.29728692441841087, 'min_samples_leaf': 34, 'n_estimators': 48, 'random_state': 40}
第181次，测试集正确率为： 0.7228381374722838
{'bootstrap':

...

{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 36, 'max_features': 0.31986764094619924, 'min_samples_leaf': 3, 'n_estimators': 31, 'random_state': 40}
第9793次，测试集正确率为： 0.8603104212860311
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 36, 'max_features': 0.32557253947577375, 'min_samples_leaf': 20, 'n_estimators': 31, 'random_state': 40}
第9794次，测试集正确率为： 0.7893569844789357
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 36, 'max_features': 0.28459513380502355, 'min_samples_leaf': 75, 'n_estimators': 31, 'random_state': 40}
第9795次，测试集正确率为： 0.6917960088691796
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 17, 'max_features': 0.3286210584487989, 'min_samples_leaf': 3, 'n_estimators': 33, 'random_state': 40}
第9796次，测试集正确率为： 0.8603104212860311
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 17, 'max_features': 0.3079906982286253, 'min_samples_leaf': 59, 'n_estimators': 42, 'random_state': 40}
第9797次，测试集正确率为： 0.70509977827051
{'bootstrap': 0, 'criterion': 'gini'

{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 15, 'max_features': 0.30027358683891797, 'min_samples_leaf': 3, 'n_estimators': 33, 'random_state': 40}
第9836次，测试集正确率为： 0.8603104212860311
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 15, 'max_features': 0.34651314612750683, 'min_samples_leaf': 73, 'n_estimators': 28, 'random_state': 40}
第9837次，测试集正确率为： 0.6829268292682927
{'bootstrap': 1, 'criterion': 'entropy', 'max_depth': 15, 'max_features': 0.29306394436107175, 'min_samples_leaf': 3, 'n_estimators': 33, 'random_state': 40}
第9838次，测试集正确率为： 0.8425720620842572
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 18, 'max_features': 0.3467983618893757, 'min_samples_leaf': 28, 'n_estimators': 10, 'random_state': 40}
第9839次，测试集正确率为： 0.720620842572062
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 36, 'max_features': 0.5020544574305553, 'min_samples_leaf': 17, 'n_estimators': 56, 'random_state': 40}
第9840次，测试集正确率为： 0.7649667405764967
{'bootstrap': 0, 'criterion': 'entr

{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 27, 'max_features': 0.33039162569329966, 'min_samples_leaf': 71, 'n_estimators': 33, 'random_state': 40}
第9879次，测试集正确率为： 0.6962305986696231
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 36, 'max_features': 0.27070986263918634, 'min_samples_leaf': 29, 'n_estimators': 26, 'random_state': 40}
第9880次，测试集正确率为： 0.7184035476718403
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 36, 'max_features': 0.29126660629345946, 'min_samples_leaf': 3, 'n_estimators': 55, 'random_state': 40}
第9881次，测试集正确率为： 0.8425720620842572
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 25, 'max_features': 0.298554702552339, 'min_samples_leaf': 33, 'n_estimators': 4, 'random_state': 40}
第9882次，测试集正确率为： 0.6984478935698448
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 18, 'max_features': 0.322101201219008, 'min_samples_leaf': 9, 'n_estimators': 43, 'random_state': 40}
第9883次，测试集正确率为： 0.8048780487804879
{'bootstrap': 0, 'criterion': 'entrop

第9921次，测试集正确率为： 0.835920177383592
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 23, 'max_features': 0.27857101055183703, 'min_samples_leaf': 19, 'n_estimators': 60, 'random_state': 40}
第9922次，测试集正确率为： 0.8004434589800443
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 18, 'max_features': 0.2799583706478318, 'min_samples_leaf': 6, 'n_estimators': 31, 'random_state': 40}
第9923次，测试集正确率为： 0.8337028824833703
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 20, 'max_features': 0.32710743456129426, 'min_samples_leaf': 41, 'n_estimators': 3, 'random_state': 40}
第9924次，测试集正确率为： 0.6807095343680709
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 4, 'max_features': 0.31283044403006544, 'min_samples_leaf': 74, 'n_estimators': 49, 'random_state': 40}
第9925次，测试集正确率为： 0.6940133037694013
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 18, 'max_features': 0.3403061259400764, 'min_samples_leaf': 5, 'n_estimators': 38, 'random_state': 40}
第9926次，测试集正确率为： 0.8159645232815964
{'

{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 18, 'max_features': 0.30227403699862704, 'min_samples_leaf': 79, 'n_estimators': 25, 'random_state': 40}
第9965次，测试集正确率为： 0.7161862527716186
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 25, 'max_features': 0.2951252357038024, 'min_samples_leaf': 4, 'n_estimators': 33, 'random_state': 40}
第9966次，测试集正确率为： 0.8159645232815964
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 23, 'max_features': 0.33266287609217515, 'min_samples_leaf': 25, 'n_estimators': 10, 'random_state': 40}
第9967次，测试集正确率为： 0.738359201773836
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 17, 'max_features': 0.3371419272160334, 'min_samples_leaf': 35, 'n_estimators': 50, 'random_state': 40}
第9968次，测试集正确率为： 0.7184035476718403
{'bootstrap': 0, 'criterion': 'entropy', 'max_depth': 25, 'max_features': 0.3033867433479352, 'min_samples_leaf': 51, 'n_estimators': 33, 'random_state': 40}
第9969次，测试集正确率为： 0.7006651884700665
{'bootstrap': 0, 'criterion': 'entr

In [25]:
%%time

classifier = RandomForestClassifier(bootstrap= 0, criterion= 'entropy', max_depth=24,
                                    max_features= 0.3090928393734417, min_samples_leaf= 2,
                                    n_estimators= 30, random_state= 40)
classifier.fit(train, label)  
#print(accuracy_score(valid_target, classifier.predict(valid_data)))

prediction = classifier.predict(test)

CPU times: user 116 ms, sys: 2.52 ms, total: 119 ms
Wall time: 119 ms


In [26]:
test["User-Item1-Item2"] = test['usr_id'].map(str)+'-'+test['item1_id'].map(str)+'-'+test['item2_id'].map(str)
test['Preference'] = prediction.astype(np.int8)

submission = test[['User-Item1-Item2','Preference']]

submission.to_csv('submission4_Forest.csv',index = False)

In [28]:
classifier.feature_importances_

array([0.04280312, 0.05889861, 0.01937631, 0.00549956, 0.0080632 ,
       0.00387221, 0.00603724, 0.03760694, 0.05028153, 0.02350511,
       0.05920599, 0.03251297, 0.06580344, 0.0280479 , 0.0554469 ,
       0.02063143, 0.05005813, 0.04939939, 0.04875045, 0.05850763,
       0.04525894, 0.05698366, 0.0422543 , 0.01890855, 0.0223705 ,
       0.02578853, 0.03213237, 0.03199511])

In [ ]:
#train_data, valid_data, train_target, valid_target

from sklearn.metrics import accuracy_score
from hyperopt import fmin, tpe, hp, rand
import lightgbm as lgb

'''d_train = lgb.Dataset(train_data, train_target)
d_valid = lgb.Dataset(valid_data, valid_target)'''

parameter_space_lgb ={
    'objective' :'binary',
    'metric': 'binary_logloss',
    'boost' : hp.choice('boost',['gbdt', 'rf', 'dart', 'goss']),
    'learning_rate':hp.uniform('learning_rate',0.01,0.2),
    'num_leaves':hp.randint('num_leaves',100)+2,
    'tree_learner':hp.choice('tree_learner',['serial', 'feature', 'data', 'voting']),
    'num_threads':2,
    'min_data_in_leaf':hp.randint('min_data_in_leaf',80)+1,
    'feature_fraction':hp.uniform('feature_fraction', 0.2, 0.8),
    'bagging_fraction':hp.uniform('bagging_fraction', 0.2, 0.8),
    'bagging_freq': hp.randint('bagging_freq',4)+1
    
}

count = 0

def function(args):
    print(args)

    # **可以把dict转换为关键字参数，可以大大简化复杂的函数调用
    clf = lgb.LGBMClassifier(**args )
    clf.fit(train_data,train_target)
    # 预测测试集
    prediction = clf.predict(valid_data)

    global count
    count = count + 1
    score = accuracy_score(valid_target, prediction)
    print("第%s次，测试集正确率为：" % str(count),score)

    # 由于hyperopt仅提供fmin接口，因此如果要求最大值，则需要取相反数
    return -score

# algo指定搜索算法，目前支持以下算法：
# ①随机搜索(hyperopt.rand.suggest)
# ②模拟退火(hyperopt.anneal.suggest)
# ③TPE算法（hyperopt.tpe.suggest，算法全称为Tree-structured Parzen Estimator Approach）
# max_evals指定枚举次数上限，即使第max_evals次枚举仍未能确定全局最优解，也要结束搜索，返回目前搜索到的最优解

best = fmin(function, parameter_space_lgb, algo=tpe.suggest, max_evals=10000)

# best["kernel"]返回的是数组下标，因此需要把它还原回来
boost_list = ['gbdt', 'rf', 'dart', 'goss']
best["boost"] = boost_list[best["boost"]]

tree_learner_list = ['serial', 'feature', 'data', 'voting']
best["tree_learner"] = tree_learner_list[best["tree_learner"]]

print("最佳参数为：",best)





In [31]:
import lightgbm as lgb

#test = test.drop(columns=['User-Item1-Item2','Preference'])
clf = lgb.LGBMClassifier(bagging_fraction= 0.7153276270227718, bagging_freq= 1, boost= 'rf',
                         feature_fraction= 0.6713679392414936, learning_rate= 0.14696807606745488,
                         metric= 'binary_logloss', min_data_in_leaf= 51, num_leaves= 52,
                         num_threads= 2, objective= 'binary', tree_learner= 'voting')
clf.fit(train,label)
# 预测测试集
prediction = clf.predict(test)

test["User-Item1-Item2"] = test['usr_id'].map(str)+'-'+test['item1_id'].map(str)+'-'+test['item2_id'].map(str)
test['Preference'] = prediction.astype(np.int8)

submission = test[['User-Item1-Item2','Preference']]

submission.to_csv('submission8_Lgb.csv',index = False)

/usr/local/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:


In [32]:
clf.feature_importances_

array([ 67,  85,  81,   8,  24,   7,  27,  53,  32,  36,  34,  45,  33,
        42,  41,  53,  43,  48,  30,  49,  52,  60,  38,  47,  38,  26,
       160,  83])

In [112]:

neigh = KNeighborsClassifier(n_neighbors=3)
neigh.fit(train_data,train_target) 
prediction = neigh.predict(valid_data)
score = accuracy_score(valid_target, prediction)

In [116]:
#train_data, valid_data, train_target, valid_target

from sklearn.metrics import accuracy_score
from hyperopt import fmin, tpe, hp, rand
from sklearn.neighbors import KNeighborsClassifier

parameter_space_knn ={
    'n_neighbors' :hp.randint('n_neighbors',8)+2,
    'weights' : hp.choice('weights',['uniform', 'distance']),
    'leaf_size':hp.randint('leaf_size',50)+2,
    'p':hp.choice('p',[1, 2])    
}

count = 0

def function(args):
    print(args)

    # **可以把dict转换为关键字参数，可以大大简化复杂的函数调用
    clf = KNeighborsClassifier(**args)
    clf.fit(train_data,train_target)
    # 预测测试集
    prediction = clf.predict(valid_data)

    global count
    count = count + 1
    score = accuracy_score(valid_target, prediction)
    print("第%s次，测试集正确率为：" % str(count),score)

    # 由于hyperopt仅提供fmin接口，因此如果要求最大值，则需要取相反数
    return -score

# algo指定搜索算法，目前支持以下算法：
# ①随机搜索(hyperopt.rand.suggest)
# ②模拟退火(hyperopt.anneal.suggest)
# ③TPE算法（hyperopt.tpe.suggest，算法全称为Tree-structured Parzen Estimator Approach）
# max_evals指定枚举次数上限，即使第max_evals次枚举仍未能确定全局最优解，也要结束搜索，返回目前搜索到的最优解

best = fmin(function, parameter_space_knn, algo=tpe.suggest, max_evals=10000)

# best["kernel"]返回的是数组下标，因此需要把它还原回来
p_list = [1,2]
best["p"] = p_list[best["p"]]

weights_list = ['uniform', 'distance']
best["weights"] = weights_list[best["weights"]]

print("最佳参数为：",best)





{'leaf_size': 19, 'n_neighbors': 8, 'p': 1, 'weights': 'distance'}
第1次，测试集正确率为： 0.7006651884700665
{'leaf_size': 38, 'n_neighbors': 2, 'p': 1, 'weights': 'uniform'}
第2次，测试集正确率为： 0.6518847006651884
{'leaf_size': 31, 'n_neighbors': 2, 'p': 2, 'weights': 'uniform'}
第3次，测试集正确率为： 0.5898004434589801
{'leaf_size': 37, 'n_neighbors': 2, 'p': 1, 'weights': 'uniform'}
第4次，测试集正确率为： 0.6518847006651884
{'leaf_size': 17, 'n_neighbors': 6, 'p': 2, 'weights': 'uniform'}
第5次，测试集正确率为： 0.5853658536585366
{'leaf_size': 35, 'n_neighbors': 4, 'p': 1, 'weights': 'distance'}
第6次，测试集正确率为： 0.6962305986696231
{'leaf_size': 7, 'n_neighbors': 4, 'p': 1, 'weights': 'uniform'}
第7次，测试集正确率为： 0.6674057649667405
{'leaf_size': 6, 'n_neighbors': 3, 'p': 1, 'weights': 'uniform'}
第8次，测试集正确率为： 0.6718403547671841
{'leaf_size': 50, 'n_neighbors': 3, 'p': 2, 'weights': 'uniform'}
第9次，测试集正确率为： 0.6031042128603105
{'leaf_size': 28, 'n_neighbors': 8, 'p': 2, 'weights': 'uniform'}
第10次，测试集正确率为： 0.5764966740576497
{'leaf_size': 5, 'n

{'leaf_size': 7, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第88次，测试集正确率为： 0.6962305986696231
{'leaf_size': 8, 'n_neighbors': 5, 'p': 2, 'weights': 'uniform'}
第89次，测试集正确率为： 0.5587583148558758
{'leaf_size': 24, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第90次，测试集正确率为： 0.7028824833702882
{'leaf_size': 24, 'n_neighbors': 4, 'p': 1, 'weights': 'distance'}
第91次，测试集正确率为： 0.6917960088691796
{'leaf_size': 5, 'n_neighbors': 6, 'p': 1, 'weights': 'distance'}
第92次，测试集正确率为： 0.6940133037694013
{'leaf_size': 25, 'n_neighbors': 8, 'p': 1, 'weights': 'uniform'}
第93次，测试集正确率为： 0.6762749445676275
{'leaf_size': 26, 'n_neighbors': 5, 'p': 2, 'weights': 'distance'}
第94次，测试集正确率为： 0.5742793791574279
{'leaf_size': 33, 'n_neighbors': 9, 'p': 1, 'weights': 'distance'}
第95次，测试集正确率为： 0.7006651884700665
{'leaf_size': 51, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第96次，测试集正确率为： 0.7028824833702882
{'leaf_size': 27, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第97次，测试集正确率为： 0.6984478935698448
{'lea

第174次，测试集正确率为： 0.7028824833702882
{'leaf_size': 42, 'n_neighbors': 4, 'p': 1, 'weights': 'distance'}
第175次，测试集正确率为： 0.6962305986696231
{'leaf_size': 39, 'n_neighbors': 8, 'p': 1, 'weights': 'distance'}
第176次，测试集正确率为： 0.6984478935698448
{'leaf_size': 8, 'n_neighbors': 5, 'p': 1, 'weights': 'uniform'}
第177次，测试集正确率为： 0.6762749445676275
{'leaf_size': 5, 'n_neighbors': 7, 'p': 2, 'weights': 'distance'}
第178次，测试集正确率为： 0.6053215077605322
{'leaf_size': 18, 'n_neighbors': 6, 'p': 1, 'weights': 'distance'}
第179次，测试集正确率为： 0.6940133037694013
{'leaf_size': 49, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第180次，测试集正确率为： 0.7028824833702882
{'leaf_size': 25, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第181次，测试集正确率为： 0.6984478935698448
{'leaf_size': 32, 'n_neighbors': 9, 'p': 1, 'weights': 'distance'}
第182次，测试集正确率为： 0.7006651884700665
{'leaf_size': 12, 'n_neighbors': 5, 'p': 1, 'weights': 'uniform'}
第183次，测试集正确率为： 0.6762749445676275
{'leaf_size': 33, 'n_neighbors': 2, 'p': 2, 'weights': 'dista

第256次，测试集正确率为： 0.6807095343680709
{'leaf_size': 16, 'n_neighbors': 5, 'p': 2, 'weights': 'distance'}
第257次，测试集正确率为： 0.5742793791574279
{'leaf_size': 35, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第258次，测试集正确率为： 0.7028824833702882
{'leaf_size': 16, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第259次，测试集正确率为： 0.7028824833702882
{'leaf_size': 16, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第260次，测试集正确率为： 0.7028824833702882
{'leaf_size': 16, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第261次，测试集正确率为： 0.7028824833702882
{'leaf_size': 51, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第262次，测试集正确率为： 0.7028824833702882
{'leaf_size': 33, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第263次，测试集正确率为： 0.7028824833702882
{'leaf_size': 12, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第264次，测试集正确率为： 0.7006651884700665
{'leaf_size': 17, 'n_neighbors': 9, 'p': 1, 'weights': 'distance'}
第265次，测试集正确率为： 0.7006651884700665
{'leaf_size': 47, 'n_neighbors': 7, 'p': 1, 'weights': 'd

{'leaf_size': 4, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第339次，测试集正确率为： 0.6962305986696231
{'leaf_size': 29, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第340次，测试集正确率为： 0.7028824833702882
{'leaf_size': 12, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第341次，测试集正确率为： 0.7006651884700665
{'leaf_size': 11, 'n_neighbors': 6, 'p': 2, 'weights': 'uniform'}
第342次，测试集正确率为： 0.5875831485587583
{'leaf_size': 39, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第343次，测试集正确率为： 0.7028824833702882
{'leaf_size': 32, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第344次，测试集正确率为： 0.7028824833702882
{'leaf_size': 10, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第345次，测试集正确率为： 0.7006651884700665
{'leaf_size': 25, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第346次，测试集正确率为： 0.6984478935698448
{'leaf_size': 38, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第347次，测试集正确率为： 0.7028824833702882
{'leaf_size': 44, 'n_neighbors': 2, 'p': 1, 'weights': 'distance'}
第348次，测试集正确率为： 0.667405764

...

{'leaf_size': 3, 'n_neighbors': 9, 'p': 1, 'weights': 'distance'}
第9627次，测试集正确率为： 0.7028824833702882
{'leaf_size': 3, 'n_neighbors': 9, 'p': 1, 'weights': 'distance'}
第9628次，测试集正确率为： 0.7028824833702882
{'leaf_size': 3, 'n_neighbors': 9, 'p': 1, 'weights': 'distance'}
第9629次，测试集正确率为： 0.7028824833702882
{'leaf_size': 24, 'n_neighbors': 9, 'p': 1, 'weights': 'distance'}
第9630次，测试集正确率为： 0.7006651884700665
{'leaf_size': 27, 'n_neighbors': 9, 'p': 1, 'weights': 'distance'}
第9631次，测试集正确率为： 0.7006651884700665
{'leaf_size': 27, 'n_neighbors': 9, 'p': 1, 'weights': 'distance'}
第9632次，测试集正确率为： 0.7006651884700665
{'leaf_size': 5, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9633次，测试集正确率为： 0.6962305986696231
{'leaf_size': 43, 'n_neighbors': 9, 'p': 1, 'weights': 'distance'}
第9634次，测试集正确率为： 0.7006651884700665
{'leaf_size': 29, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9635次，测试集正确率为： 0.7028824833702882
{'leaf_size': 27, 'n_neighbors': 9, 'p': 1, 'weights': 'distance'}
第9636次，测试集正确率为： 0.7

{'leaf_size': 32, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9708次，测试集正确率为： 0.7028824833702882
{'leaf_size': 32, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9709次，测试集正确率为： 0.7028824833702882
{'leaf_size': 50, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9710次，测试集正确率为： 0.7028824833702882
{'leaf_size': 50, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9711次，测试集正确率为： 0.7028824833702882
{'leaf_size': 25, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9712次，测试集正确率为： 0.7028824833702882
{'leaf_size': 25, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9713次，测试集正确率为： 0.7028824833702882
{'leaf_size': 50, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9714次，测试集正确率为： 0.7028824833702882
{'leaf_size': 50, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9715次，测试集正确率为： 0.7028824833702882
{'leaf_size': 25, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9716次，测试集正确率为： 0.7028824833702882
{'leaf_size': 25, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9717次，测试集正确率为：

{'leaf_size': 43, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9789次，测试集正确率为： 0.7028824833702882
{'leaf_size': 43, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9790次，测试集正确率为： 0.7028824833702882
{'leaf_size': 43, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9791次，测试集正确率为： 0.7028824833702882
{'leaf_size': 43, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9792次，测试集正确率为： 0.7028824833702882
{'leaf_size': 43, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9793次，测试集正确率为： 0.7028824833702882
{'leaf_size': 43, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9794次，测试集正确率为： 0.7028824833702882
{'leaf_size': 43, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9795次，测试集正确率为： 0.7028824833702882
{'leaf_size': 43, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9796次，测试集正确率为： 0.7028824833702882
{'leaf_size': 10, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9797次，测试集正确率为： 0.7006651884700665
{'leaf_size': 43, 'n_neighbors': 5, 'p': 1, 'weights': 'uniform'}
第9798次，测试集正确率为： 

{'leaf_size': 41, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9870次，测试集正确率为： 0.7028824833702882
{'leaf_size': 41, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9871次，测试集正确率为： 0.7028824833702882
{'leaf_size': 51, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9872次，测试集正确率为： 0.7028824833702882
{'leaf_size': 51, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9873次，测试集正确率为： 0.7028824833702882
{'leaf_size': 51, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9874次，测试集正确率为： 0.7028824833702882
{'leaf_size': 51, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9875次，测试集正确率为： 0.7028824833702882
{'leaf_size': 51, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9876次，测试集正确率为： 0.7028824833702882
{'leaf_size': 51, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9877次，测试集正确率为： 0.7028824833702882
{'leaf_size': 51, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9878次，测试集正确率为： 0.7028824833702882
{'leaf_size': 51, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9879次，测试集正确率为：

{'leaf_size': 26, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9952次，测试集正确率为： 0.6984478935698448
{'leaf_size': 13, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9953次，测试集正确率为： 0.7006651884700665
{'leaf_size': 26, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9954次，测试集正确率为： 0.6984478935698448
{'leaf_size': 26, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9955次，测试集正确率为： 0.6984478935698448
{'leaf_size': 26, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9956次，测试集正确率为： 0.6984478935698448
{'leaf_size': 14, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9957次，测试集正确率为： 0.7006651884700665
{'leaf_size': 26, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9958次，测试集正确率为： 0.6984478935698448
{'leaf_size': 26, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9959次，测试集正确率为： 0.6984478935698448
{'leaf_size': 48, 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
第9960次，测试集正确率为： 0.7028824833702882
{'leaf_size': 26, 'n_neighbors': 7, 'p': 1, 'weights': 'distance'}
第9961次，测试集正确率为：